# `pandas` Part I

This document includes a sequence of notebooks to introduce data manipulation in Python using the `pandas` library.

## Basic building blocks
`pandas` works with tabular data (rows and columns) through `Series`, `DataFrame` objects.

In [11]:
import pandas as pd

meteor = pd.read_csv('../data/Meteorite_Landings.csv')

*Source: [NASA Open Data Portal](https://data.nasa.gov/Space-Science/Meteorite-Landings/gh4g-9sfh/data_preview)*

In [ ]:
type(meteor)

A `DataFrame` is the basic "spreadsheet" or "table" used in Python.  A `DataFrame` object is composed of one or more `Series` objects (columns), and indexed by `Index` (rows).

In [ ]:
# head.() shows us the first several rows
meteor.head()

In [ ]:
# investigate a column (note its type)
print(type(meteor.name))

meteor.name.head()

In [ ]:
# investigate how the columns are labeled
meteor.columns

In [ ]:
# investigate how the rows are indexed
meteor.index

## DataFrame sources

`DataFrame`s can be created from reading a file, scraping the web, and/or API requests.  

### Reading from a file

In [ ]:
import pandas as pd

meteor = pd.read_csv('../data/Meteorite_Landings.csv')

### API requests (more details later)

In [1]:
import requests

response = requests.get(
    'https://data.nasa.gov/resource/gh4g-9sfh.json',
    params={'$limit': 50000}  # Depending on the API, there may be a default limit of records one can obtain
)  

In [2]:
response  # A 200 exit code indicates success

<Response [200]>

*Tip:* A list of HTTP GET exit codes is available at https://developer.mozilla.org/en-US/docs/Web/HTTP/Status.

In [3]:
response.ok  # checks ok flag

True

In [4]:
# Extract data if request is successful
if response.ok:
    payload = response.json()
else:
    print(f'Request failed with exit code {response.status_code}.')
    payload = None

In [7]:
# Load into DataFrame
meteor_json = pd.DataFrame(payload)
meteor_json.head()

name   id nametype     recclass    mass  fall                     year  \
0    Aachen    1    Valid           L5      21  Fell  1880-01-01T00:00:00.000   
1    Aarhus    2    Valid           H6     720  Fell  1951-01-01T00:00:00.000   
2      Abee    6    Valid          EH4  107000  Fell  1952-01-01T00:00:00.000   
3  Acapulco   10    Valid  Acapulcoite    1914  Fell  1976-01-01T00:00:00.000   
4   Achiras  370    Valid           L6     780  Fell  1902-01-01T00:00:00.000   

       reclat      reclong                                        geolocation  \
0   50.775000     6.083330     {'latitude': '50.775', 'longitude': '6.08333'}   
1   56.183330    10.233330  {'latitude': '56.18333', 'longitude': '10.23333'}   
2   54.216670  -113.000000    {'latitude': '54.21667', 'longitude': '-113.0'}   
3   16.883330   -99.900000     {'latitude': '16.88333', 'longitude': '-99.9'}   
4  -33.166670   -64.950000   {'latitude': '-33.16667', 'longitude': '-64.95'}   

  :@computed_region_cbhk_fwbd :@computed_region_nnqa_25f4  
0                         NaN                         NaN  
1                         NaN                         NaN  
2                         NaN                         NaN  
3                         NaN                         NaN  
4                         NaN                         NaN

In [8]:
# Removing auto-computed columns
mask = meteor_json.columns.str.contains('@computed_region', regex=True)

columns_to_drop = meteor_json.columns[mask]

In [9]:
meteor_json = meteor_json.drop(columns=columns_to_drop)

In [10]:
# storing downloaded data into files
# meteor_json.to_csv('meteor.csv')  

## Basic inspection

### What type of data are available in the dataframe? Are there missing data?

In [ ]:
meteor.info()

### How much data are available?

In [ ]:
meteor.shape

## Subsetting and indexing

Effectively extracting data from a full dataset requires fluency in how the `DataFrame` can be subsetted and how it is indexed.

### Calling a column by attributes (if valid)

In [ ]:
meteor.recclass

### Calling a column by keys

In [ ]:
meteor['mass (g)']

### Multiple columns by name

In [17]:
meteor[['name', 'mass (g)']]

name  mass (g)
0          Aachen      21.0
1          Aarhus     720.0
2            Abee  107000.0
3        Acapulco    1914.0
4         Achiras     780.0
...           ...       ...
45711  Zillah 002     172.0
45712      Zinder      46.0
45713        Zlin       3.3
45714   Zubkovsky    2167.0
45715  Zulu Queen     200.0

[45716 rows x 2 columns]

### Selecting rows

In [18]:
meteor[5:10]  # end-exclusive

name   id nametype recclass  mass (g)  fall    year  \
5             Adhi Kot  379    Valid      EH4    4239.0  Fell  1919.0   
6  Adzhi-Bogdo (stone)  390    Valid    LL3-6     910.0  Fell  1949.0   
7                 Agen  392    Valid       H5   30000.0  Fell  1814.0   
8               Aguada  398    Valid       L6    1620.0  Fell  1930.0   
9        Aguila Blanca  417    Valid        L    1440.0  Fell  1920.0   

     reclat   reclong           GeoLocation  
5  32.10000  71.80000          (32.1, 71.8)  
6  44.83333  95.16667  (44.83333, 95.16667)  
7  44.21667   0.61667   (44.21667, 0.61667)  
8 -31.60000 -65.23333    (-31.6, -65.23333)  
9 -30.86667 -64.55000   (-30.86667, -64.55)

### Indexing with `.loc[]`, `iloc[]`

- `.loc[]` indexes by row labels
- `.iloc[]` indexes by indices

In [19]:
meteor.loc[0:4, 'name':'mass (g)']

name   id nametype     recclass  mass (g)
0    Aachen    1    Valid           L5      21.0
1    Aarhus    2    Valid           H6     720.0
2      Abee    6    Valid          EH4  107000.0
3  Acapulco   10    Valid  Acapulcoite    1914.0
4   Achiras  370    Valid           L6     780.0

In [20]:
meteor.iloc[0:4, 0:5]

name  id nametype     recclass  mass (g)
0    Aachen   1    Valid           L5      21.0
1    Aarhus   2    Valid           H6     720.0
2      Abee   6    Valid          EH4  107000.0
3  Acapulco  10    Valid  Acapulcoite    1914.0

### Filtering or subsetting by condition
Selection by condition can be performed by creating a Boolean *mask* with True/False values to specify which rows/columns to select.

In [21]:
# select records with heavy meteor (mass > 10^7) that are found (fall = 'Found')
mask = (meteor['mass (g)'] > 1e7) & (meteor.fall == 'Found')
mask

0        False
1        False
2        False
3        False
4        False
         ...  
45711    False
45712    False
45713    False
45714    False
45715    False
Length: 45716, dtype: bool

**Note:** Each condition is surrounded by parentheses, and we use bitwise operator (`&`, `|`, `~`) instead of logical operators (`and`, `or`, `not`).

In [22]:
meteor[mask]

name     id nametype         recclass    mass (g)   fall  \
3455           Armanty   2335    Valid       Iron, IIIE  28000000.0  Found   
5016        Bacubirito   4919    Valid  Iron, ungrouped  22000000.0  Found   
5365   Campo del Cielo   5247    Valid     Iron, IAB-MG  50000000.0  Found   
5370     Canyon Diablo   5257    Valid     Iron, IAB-MG  30000000.0  Found   
5373         Cape York   5262    Valid      Iron, IIIAB  58200000.0  Found   
5468        Chupaderos   5363    Valid      Iron, IIIAB  24300000.0  Found   
12613           Gibeon  10912    Valid        Iron, IVA  26000000.0  Found   
16392             Hoba  11890    Valid        Iron, IVB  60000000.0  Found   
22921            Mbosi  15456    Valid  Iron, ungrouped  16000000.0  Found   
26174           Morito  16745    Valid      Iron, IIIAB  10100000.0  Found   
26297      Mundrabilla  16852    Valid    Iron, IAB-ung  24000000.0  Found   
38317       Willamette  24269    Valid      Iron, IIIAB  15500000.0  Found   

         year    reclat    reclong             GeoLocation  
3455   1898.0  47.00000   88.00000            (47.0, 88.0)  
5016   1863.0  26.20000 -107.83333      (26.2, -107.83333)  
5365   1575.0 -27.46667  -60.58333  (-27.46667, -60.58333)  
5370   1891.0  35.05000 -111.03333     (35.05, -111.03333)  
5373   1818.0  76.13333  -64.93333   (76.13333, -64.93333)  
5468   1852.0  27.00000 -105.10000          (27.0, -105.1)  
12613  1836.0 -25.50000   18.00000           (-25.5, 18.0)  
16392  1920.0 -19.58333   17.91667   (-19.58333, 17.91667)  
22921  1930.0  -9.11667   33.06667    (-9.11667, 33.06667)  
26174  1600.0  27.05000 -105.43333     (27.05, -105.43333)  
26297  1911.0 -30.78333  127.55000     (-30.78333, 127.55)  
38317  1902.0  45.36667 -122.58333  (45.36667, -122.58333)

In [ ]:
# negation of a mask
meteor[~mask]

**Note**: Boolean masks can be used with `loc[]` and `iloc[]` as well.

## Calculating summary statistics
This section discusses preliminary calculations before conducting further data analysis.

### How many of the meteorites were observed falling vs found?

In [23]:
meteor.fall.value_counts()

fall
Found    44609
Fell      1107
Name: count, dtype: int64

In [24]:
meteor.fall.value_counts(normalize=True)

fall
Found    0.975785
Fell     0.024215
Name: proportion, dtype: float64

### Behavior of mass of a meterorite?

In [ ]:
meteor['mass (g)'].mean()

In [ ]:
meteor['mass (g)'].quantile([0.01, 0.05, 0.5, 0.95, 0.99])

In [ ]:
meteor['mass (g)'].max()

In [28]:
# sometimes helpful to locate the other information related to a particular entry
meteor['mass (g)'].idxmax()
meteor.loc[meteor['mass (g)'].idxmax()]  # note the "index" of max()

name                            Hoba
id                             11890
nametype                       Valid
recclass                   Iron, IVB
mass (g)                  60000000.0
fall                           Found
year                          1920.0
reclat                     -19.58333
reclong                     17.91667
GeoLocation    (-19.58333, 17.91667)
Name: 16392, dtype: object

### How many unique classes are in this dataset?

In [30]:
meteor.recclass.unique()

array(['L5', 'H6', 'EH4', 'Acapulcoite', 'L6', 'LL3-6', 'H5', 'L',
       'Diogenite-pm', 'Unknown', 'H4', 'H', 'Iron, IVA', 'CR2-an', 'LL5',
       'CI1', 'L/LL4', 'Eucrite-mmict', 'CV3', 'Ureilite-an',
       'Stone-uncl', 'L3', 'Angrite', 'LL6', 'L4', 'Aubrite',
       'Iron, IIAB', 'Iron, IAB-sLL', 'Iron, ungrouped', 'CM2', 'OC',
       'Mesosiderite-A1', 'LL4', 'C2-ung', 'LL3.8', 'Howardite',
       'Eucrite-pmict', 'Diogenite', 'LL3.15', 'LL3.9', 'Iron, IAB-MG',
       'H/L3.9', 'Iron?', 'Eucrite', 'H4-an', 'L/LL6', 'Iron, IIIAB',
       'H/L4', 'H4-5', 'L3.7', 'LL3.4', 'Martian (chassignite)', 'EL6',
       'H3.8', 'H3-5', 'H5-6', 'Mesosiderite', 'H5-7', 'L3-6', 'H4-6',
       'Ureilite', 'Iron, IID', 'Mesosiderite-A3/4', 'CO3.3', 'H3',
       'EH3/4-an', 'Iron, IIE', 'L/LL5', 'H3.7', 'CBa', 'H4/5', 'H3/4',
       'H?', 'H3-6', 'L3.4', 'Iron, IAB-sHL', 'L3.7-6', 'EH7-an', 'Iron',
       'CR2', 'CO3.2', 'K3', 'L5/6', 'CK4', 'Iron, IIE-an', 'L3.6',
       'LL3.2', 'Pallasite', 'CO

### General statistics
The `.describe()` method includes numeric columns by default.  Here we can force it to include all columns.

In [33]:
meteor.describe(include='all')

name            id nametype recclass      mass (g)   fall  \
count    45716  45716.000000    45716    45716  4.558500e+04  45716   
unique   45716           NaN        2      466           NaN      2   
top     Aachen           NaN    Valid       L6           NaN  Found   
freq         1           NaN    45641     8285           NaN  44609   
mean       NaN  26889.735104      NaN      NaN  1.327808e+04    NaN   
std        NaN  16860.683030      NaN      NaN  5.749889e+05    NaN   
min        NaN      1.000000      NaN      NaN  0.000000e+00    NaN   
25%        NaN  12688.750000      NaN      NaN  7.200000e+00    NaN   
50%        NaN  24261.500000      NaN      NaN  3.260000e+01    NaN   
75%        NaN  40656.750000      NaN      NaN  2.026000e+02    NaN   
max        NaN  57458.000000      NaN      NaN  6.000000e+07    NaN   

                year        reclat       reclong GeoLocation  
count   45425.000000  38401.000000  38401.000000       38401  
unique           NaN           NaN           NaN       17100  
top              NaN           NaN           NaN  (0.0, 0.0)  
freq             NaN           NaN           NaN        6214  
mean     1991.828817    -39.122580     61.074319         NaN  
std        25.052766     46.378511     80.647298         NaN  
min       860.000000    -87.366670   -165.433330         NaN  
25%      1987.000000    -76.714240      0.000000         NaN  
50%      1998.000000    -71.500000     35.666670         NaN  
75%      2003.000000      0.000000    157.166670         NaN  
max      2101.000000     81.166670    354.473330         NaN


**Note**: `NaN` values signify missing data. For instance, the fall column contains strings, so there is no value for mean; likewise, mass (g) is numeric, so we don't have entries for the categorical summary statistics (unique, top, freq).

## Practice: Yellow cab data

The following command downloads a `.parquet` file containing NYC Yellow Taxi data, a common storage format for moderate to large datasets.

In [ ]:
!curl -O https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_2024-01.parquet

In [34]:
taxi = pd.read_parquet('yellow_tripdata_2024-01.parquet')

1. Examine the first five rows of the dataset.

2. How much data are included in this dataset?

3. Calculate summary statistics for the `fare_amount`, `tolls_amount`, and `tip_amount`.  Do they add up to the `total_amount`?

4. Find the trip that has the longest trip by distance (`trip_distance`).

5. Compare the average `total_amount` for short versus long trips (short trip has `trip_distance` < 10).  Make sure we do not include zero-distance trips.

---

## Data cleaning
We will cover some common transformations that facilitate data analysis, including rearranging columns, type conversion, and sorting.

In [ ]:
minitaxi = taxi.sample(10000)  # down-sample our dataset for illustration

In [ ]:
minitaxi.shape

In [ ]:
minitaxi.head()

### Dropping columns

In [ ]:
# drop all id columns and the store_and_fwd_flag column
mask = minitaxi.columns.str.contains('ID$|store_and_fwd_flag', regex=True)
columns_to_drop = minitaxi.columns[mask]
columns_to_drop

In [ ]:
minitaxi = minitaxi.drop(columns=columns_to_drop)
minitaxi.head()

### Renaming columns

In [ ]:
minitaxi = minitaxi.rename(
    columns={
        'tpep_pickup_datetime': 'pickup', 
        'tpep_dropoff_datetime': 'dropoff'
    }
)
minitaxi.columns

## Examine the correct data types (type conversion)

In [ ]:
minitaxi.dtypes

In [40]:
minitaxi.info()

<class 'pandas.core.frame.DataFrame'>
Index: 9524 entries, 597270 to 2512071
Data columns (total 14 columns):
 #   Column                 Non-Null Count  Dtype         
---  ------                 --------------  -----         
 0   pickup                 9524 non-null   datetime64[us]
 1   dropoff                9524 non-null   datetime64[us]
 2   passenger_count        9524 non-null   float64       
 3   trip_distance          9524 non-null   float64       
 4   payment_type           9524 non-null   int64         
 5   fare_amount            9524 non-null   float64       
 6   extra                  9524 non-null   float64       
 7   mta_tax                9524 non-null   float64       
 8   tip_amount             9524 non-null   float64       
 9   tolls_amount           9524 non-null   float64       
 10  improvement_surcharge  9524 non-null   float64       
 11  total_amount           9524 non-null   float64       
 12  congestion_surcharge   9524 non-null   float64       
 13  

In [41]:
# cast passenger_count to integers
minitaxi['passenger_count'] = minitaxi['passenger_count'].astype(int)
minitaxi.dtypes

pickup                   datetime64[us]
dropoff                  datetime64[us]
passenger_count                   int32
trip_distance                   float64
payment_type                      int64
fare_amount                     float64
extra                           float64
mta_tax                         float64
tip_amount                      float64
tolls_amount                    float64
improvement_surcharge           float64
total_amount                    float64
congestion_surcharge            float64
Airport_fee                     float64
dtype: object

### Dropping rows with NA values

In [ ]:
minitaxi = minitaxi.dropna()

In [ ]:
minitaxi.info()

## Creating new columns

Let's calculate the following for each row:

1. elapsed time of the trip
2. the tip percentage
3. the total taxes, tolls, fees, and surcharges
4. the average speed of the taxi

In [ ]:
minitaxi = minitaxi.assign(
    elapsed_time=lambda x: x.dropoff - x.pickup,
    cost_before_tip=lambda x: x.total_amount - x.tip_amount,
    tip_pct=lambda x: x.tip_amount / x.cost_before_tip, 
    fees=lambda x: x.cost_before_tip - x.fare_amount, 
    avg_speed=lambda x: x.trip_distance.div(
        x.elapsed_time.dt.total_seconds() / 60 / 60
    )
)

In [ ]:
minitaxi.head(2)

*Notes*:

- We used `lambda` functions to 1) avoid typing taxis repeatedly and 2) be able to access the `cost_before_tip` and `elapsed_time` columns in the same method that we create them.
- To create a single new column, we can also use `df['new_col'] = <values>`.

## Sorting by values

In [ ]:
# sort by descending passenger count and pickups from earliest to latest
minitaxi.sort_values(['passenger_count', 'pickup'], ascending=[False, True]).head()

In [ ]:
# pick out the 3 trips with largest timespan
minitaxi.nlargest(3, 'elapsed_time')

## Working with index
Currently the index is simply using the row numbers, but if we wish to work with the pickup times significantly, perhaps indexing by the datetime column is more effective.

In [ ]:
minitaxi.index

### Setting index

In [ ]:
minitaxi = minitaxi.set_index('pickup')
minitaxi.head(3)

### Sorting by index

In [48]:
# sorting by indices
minitaxi = minitaxi.sort_index()
minitaxi.head()

dropoff  passenger_count  trip_distance  \
pickup                                                                    
2024-01-01 00:10:19 2024-01-01 00:22:58                1           1.92   
2024-01-01 00:15:10 2024-01-01 00:22:51                1           1.64   
2024-01-01 00:19:09 2024-01-01 00:41:03                3           9.12   
2024-01-01 00:20:34 2024-01-01 00:25:54                1           0.80   
2024-01-01 00:23:35 2024-01-01 00:49:13                1           3.08   

                     payment_type  fare_amount  extra  mta_tax  tip_amount  \
pickup                                                                       
2024-01-01 00:10:19             1         13.5    1.0      0.5        3.70   
2024-01-01 00:15:10             1         10.0    1.0      0.5        3.00   
2024-01-01 00:19:09             1         38.7    1.0      0.5        8.74   
2024-01-01 00:20:34             1          6.5    3.5      0.5        2.30   
2024-01-01 00:23:35             1         23.3    1.0      0.5        7.08   

                     tolls_amount  improvement_surcharge  total_amount  \
pickup                                                                   
2024-01-01 00:10:19           0.0                    1.0         22.20   
2024-01-01 00:15:10           0.0                    1.0         18.00   
2024-01-01 00:19:09           0.0                    1.0         52.44   
2024-01-01 00:20:34           0.0                    1.0         13.80   
2024-01-01 00:23:35           0.0                    1.0         35.38   

                     congestion_surcharge  Airport_fee    elapsed_time  \
pickup                                                                   
2024-01-01 00:10:19                   2.5          0.0 0 days 00:12:39   
2024-01-01 00:15:10                   2.5          0.0 0 days 00:07:41   
2024-01-01 00:19:09                   2.5          0.0 0 days 00:21:54   
2024-01-01 00:20:34                   2.5          0.0 0 days 00:05:20   
2024-01-01 00:23:35                   2.5          0.0 0 days 00:25:38   

                     cost_before_tip   tip_pct  fees  avg_speed  
pickup                                                           
2024-01-01 00:10:19             18.5  0.200000   5.0   9.106719  
2024-01-01 00:15:10             15.0  0.200000   5.0  12.806941  
2024-01-01 00:19:09             43.7  0.200000   5.0  24.986301  
2024-01-01 00:20:34             11.5  0.200000   5.0   9.000000  
2024-01-01 00:23:35             28.3  0.250177   5.0   7.209363

Recall how we have used `[0:4]` to locate the rows indexed 0 to 4. Since we are indexing by datetime, we can select within time ranges.

### Selecting by index

In [49]:
# selecting the taxi rides in the first 6 hours of the new year
minitaxi['2024-01-01 00:00':'2024-01-01 06:00']

dropoff  passenger_count  trip_distance  \
pickup                                                                    
2024-01-01 00:10:19 2024-01-01 00:22:58                1           1.92   
2024-01-01 00:15:10 2024-01-01 00:22:51                1           1.64   
2024-01-01 00:19:09 2024-01-01 00:41:03                3           9.12   
2024-01-01 00:20:34 2024-01-01 00:25:54                1           0.80   
2024-01-01 00:23:35 2024-01-01 00:49:13                1           3.08   
...                                 ...              ...            ...   
2024-01-01 04:53:26 2024-01-02 03:11:13                6           9.97   
2024-01-01 05:06:58 2024-01-01 05:10:03                1           0.63   
2024-01-01 05:16:59 2024-01-01 05:35:39                1           4.26   
2024-01-01 05:17:26 2024-01-01 05:22:32                1           1.90   
2024-01-01 05:29:34 2024-01-01 05:38:38                1           1.57   

                     payment_type  fare_amount  extra  mta_tax  tip_amount  \
pickup                                                                       
2024-01-01 00:10:19             1         13.5    1.0      0.5        3.70   
2024-01-01 00:15:10             1         10.0    1.0      0.5        3.00   
2024-01-01 00:19:09             1         38.7    1.0      0.5        8.74   
2024-01-01 00:20:34             1          6.5    3.5      0.5        2.30   
2024-01-01 00:23:35             1         23.3    1.0      0.5        7.08   
...                           ...          ...    ...      ...         ...   
2024-01-01 04:53:26             1         52.0    1.0      0.5        0.00   
2024-01-01 05:06:58             1          5.8    1.0      0.5        2.16   
2024-01-01 05:16:59             1         22.6    1.0      0.5        5.52   
2024-01-01 05:17:26             1         10.0    1.0      0.5        0.00   
2024-01-01 05:29:34             1         10.7    1.0      0.5        0.00   

                     tolls_amount  improvement_surcharge  total_amount  \
pickup                                                                   
2024-01-01 00:10:19           0.0                    1.0         22.20   
2024-01-01 00:15:10           0.0                    1.0         18.00   
2024-01-01 00:19:09           0.0                    1.0         52.44   
2024-01-01 00:20:34           0.0                    1.0         13.80   
2024-01-01 00:23:35           0.0                    1.0         35.38   
...                           ...                    ...           ...   
2024-01-01 04:53:26           0.0                    1.0         57.00   
2024-01-01 05:06:58           0.0                    1.0         12.96   
2024-01-01 05:16:59           0.0                    1.0         33.12   
2024-01-01 05:17:26           0.0                    1.0         15.00   
2024-01-01 05:29:34           0.0                    1.0         15.70   

                     congestion_surcharge  Airport_fee    elapsed_time  \
pickup                                                                   
2024-01-01 00:10:19                   2.5          0.0 0 days 00:12:39   
2024-01-01 00:15:10                   2.5          0.0 0 days 00:07:41   
2024-01-01 00:19:09                   2.5          0.0 0 days 00:21:54   
2024-01-01 00:20:34                   2.5          0.0 0 days 00:05:20   
2024-01-01 00:23:35                   2.5          0.0 0 days 00:25:38   
...                                   ...          ...             ...   
2024-01-01 04:53:26                   2.5          0.0 0 days 22:17:47   
2024-01-01 05:06:58                   2.5          0.0 0 days 00:03:05   
2024-01-01 05:16:59                   2.5          0.0 0 days 00:18:40   
2024-01-01 05:17:26                   2.5          0.0 0 days 00:05:06   
2024-01-01 05:29:34                   2.5          0.0 0 days 00:09:04   

                     cost_before_tip   tip_pct  fees  avg_speed  
pickup                                           

### Resetting index
We can revert any specific column index back to row numbers, **but** notice that by setting and resetting index you lose the original row numbers.

In [50]:
minitaxi = minitaxi.reset_index()
minitaxi.head()

pickup             dropoff  passenger_count  trip_distance  \
0 2024-01-01 00:10:19 2024-01-01 00:22:58                1           1.92   
1 2024-01-01 00:15:10 2024-01-01 00:22:51                1           1.64   
2 2024-01-01 00:19:09 2024-01-01 00:41:03                3           9.12   
3 2024-01-01 00:20:34 2024-01-01 00:25:54                1           0.80   
4 2024-01-01 00:23:35 2024-01-01 00:49:13                1           3.08   

   payment_type  fare_amount  extra  mta_tax  tip_amount  tolls_amount  \
0             1         13.5    1.0      0.5        3.70           0.0   
1             1         10.0    1.0      0.5        3.00           0.0   
2             1         38.7    1.0      0.5        8.74           0.0   
3             1          6.5    3.5      0.5        2.30           0.0   
4             1         23.3    1.0      0.5        7.08           0.0   

   improvement_surcharge  total_amount  congestion_surcharge  Airport_fee  \
0                    1.0         22.20                   2.5          0.0   
1                    1.0         18.00                   2.5          0.0   
2                    1.0         52.44                   2.5          0.0   
3                    1.0         13.80                   2.5          0.0   
4                    1.0         35.38                   2.5          0.0   

     elapsed_time  cost_before_tip   tip_pct  fees  avg_speed  
0 0 days 00:12:39             18.5  0.200000   5.0   9.106719  
1 0 days 00:07:41             15.0  0.200000   5.0  12.806941  
2 0 days 00:21:54             43.7  0.200000   5.0  24.986301  
3 0 days 00:05:20             11.5  0.200000   5.0   9.000000  
4 0 days 00:25:38             28.3  0.250177   5.0   7.209363

## Practice: Meteorite indexing

Using the `meteor` dataset, 

1. cast the `year` column to an integer column.
2. create a new column indicating whether the meteorite was observed falling before 1970.
3. set the index to the id column and extract all the rows with IDs between 10,036 and 10,040 (inclusive) with `loc[]`.
4. examine the `year` column to see if there are any data errors.

In [1]:
import pandas as pd

meteor = pd.read_csv('../data/Meteorite_Landings.csv')

In [4]:
#meteor = meteor.dropna()
meteor['year'] = meteor['year'].astype(int)
meteor.info()

<class 'pandas.core.frame.DataFrame'>
Index: 38115 entries, 0 to 45715
Data columns (total 10 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   name         38115 non-null  object 
 1   id           38115 non-null  int64  
 2   nametype     38115 non-null  object 
 3   recclass     38115 non-null  object 
 4   mass (g)     38115 non-null  float64
 5   fall         38115 non-null  object 
 6   year         38115 non-null  int32  
 7   reclat       38115 non-null  float64
 8   reclong      38115 non-null  float64
 9   GeoLocation  38115 non-null  object 
dtypes: float64(3), int32(1), int64(1), object(5)
memory usage: 3.1+ MB


In [5]:
meteor = meteor.set_index('id')

In [7]:
meteor.set_index('id')

KeyError: "None of ['id'] are in the columns"

In [11]:
meteor.sort_index().loc[10036:10040]

<class 'pandas.core.frame.DataFrame'>
Index: 38115 entries, 1 to 30414
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   name         38115 non-null  object 
 1   nametype     38115 non-null  object 
 2   recclass     38115 non-null  object 
 3   mass (g)     38115 non-null  float64
 4   fall         38115 non-null  object 
 5   year         38115 non-null  int32  
 6   reclat       38115 non-null  float64
 7   reclong      38115 non-null  float64
 8   GeoLocation  38115 non-null  object 
dtypes: float64(3), int32(1), object(5)
memory usage: 2.8+ MB


## *For your reference*, on the issue of indexing

[pandas 2.2 User Manual on Indexing](https://pandas.pydata.org/docs/user_guide/indexing.html)